In [3]:
from os import listdir
from langchain.document_loaders import PyPDFLoader


book_names = listdir("books\\")
documents = []

for i in book_names:
    print(i)
    docc = PyPDFLoader(file_path="books\\"+i).load()
    documents.append(docc)

M. Ashraf Rizvi - Effective Technical Communication-McGraw-Hill Education (2017).pdf
Machine - Learning - Tom Mitchell.pdf
the-art-of-seduction-robert-greene.pdf


In [4]:
#converting pagewise info to single text
from langchain.docstore.document import Document
docsss = []
for i in range(len(documents)):
    text = ""
    for y in documents[i]:
        text+=y.page_content
    docsss.append(Document(page_content = text,metadata = {'Title':book_names[i]}))

In [97]:
# print("#### Semantic Chunking ####") # TOOK 30mins

# from langchain_experimental.text_splitter import SemanticChunker
# from langchain.docstore.document import Document

# # text_splitter = SemanticChunker(OpenAIEmbeddings())
# text_splitter = SemanticChunker(
#     embedder, breakpoint_threshold_type="percentile" # "standard_deviation", "interquartile"
# )

# newdoc = []
# newdoc += text_splitter.create_documents([i.page_content for i in docsss])
# print(documents)

#### Semantic Chunking ####
[[Document(metadata={'source': 'books\\M. Ashraf Rizvi - Effective Technical Communication-McGraw-Hill Education (2017).pdf', 'page': 0}, page_content='EFFECTIVE  \nTECHNICAL  COMMUNICATION\nSECOND  EDITION'), Document(metadata={'source': 'books\\M. Ashraf Rizvi - Effective Technical Communication-McGraw-Hill Education (2017).pdf', 'page': 1}, page_content='M Ashraf Rizvi  is currently Director, Jaipuria Institute of Management, Lucknow. An \neminent academician with more than thirty years of teaching, training, consulting and \nresearch experience in India and abroad, Dr. Rizvi has taught in top institutes including \nIndian Institute of Management Indore, Indian Institute of Technology Dhanbad, and \nSultan Qaboos University, Muscat, Oman. He is widely credited for positioning IIM \nIndore as a national leader in executive education. He has also served as Chairman \nof Executive PGP Programme of IIM Indore; Coordinator for Collaboration with \nUniversity o

In [5]:

from langchain_community.vectorstores import FAISS
from langchain.text_splitter import RecursiveCharacterTextSplitter

text_splitter = RecursiveCharacterTextSplitter(
    chunk_size=1000, chunk_overlap=100,
    separators=["\n\n", "\n", ".", ";", ",", " "],
)



In [6]:
print("Chunking Documents")
docs_chunks = text_splitter.split_documents(docsss)
docs_chunks = [dchunks  for dchunks in docs_chunks if len(dchunks.page_content) > 350]

Chunking Documents


In [9]:
from langchain_community.embeddings import GPT4AllEmbeddings
from langchain_community.llms import GPT4All

model = GPT4All(model="./model/mistral-7b-openorca.Q4_0.gguf")
embedder = GPT4AllEmbeddings(model_name='all-MiniLM-L6-v2.gguf2.f16.gguf',device='gpu'
                               )

In [43]:
#parent child retrieval
from langchain.retrievers import ParentDocumentRetriever, BM25Retriever , EnsembleRetriever
from faiss import IndexFlatL2
from langchain_community.docstore.in_memory import InMemoryDocstore
from langchain.storage import InMemoryStore



seperators = ["\n\n", "\n", ".", ";", ",", " "]
parent_splitter = RecursiveCharacterTextSplitter(chunk_size = 800, chunk_overlap = 50)
child_splitter = parent_splitter = RecursiveCharacterTextSplitter(chunk_size = 200, chunk_overlap = 50)





In [12]:
def create_vecstore(documents_chnks,embedder):
    embed_dims = len(embedder.embed_query("test"))
    vecstore = FAISS(
        embedding_function=embedder,
        index=IndexFlatL2(embed_dims),
        docstore=InMemoryDocstore(),
        index_to_docstore_id={},
        normalize_L2=False
    )
    for i in range(len(docs_chunks)):
        print(f"Document {i+1} is being embedded.")
        vstore = FAISS.from_documents(documents=docs_chunks[i],embedding=embedder)
        vecstore.merge_from(vstore)
    return vecstore

def get_retrieverBM25(documents):
    docs_chunks = []
    for i in range(len(documents)):
        docs_chunks+=documents[i]
    
    return BM25Retriever.from_documents(documents=docs_chunks,search_kwargs = {"k":1})

In [16]:
# vecstore = FAISS.from_documents(documents=docs_chunks,embedding=embedder)

#saving the embeddings

# vecstore.save_local("simpledocstore_index")
# !tar czvf docstore_index.tgz docstore_index

#loading the embeddings
vecstore = FAISS.load_local("docstore_index", embedder,allow_dangerous_deserialization=True)

In [74]:
retreiver1 = ParentDocumentRetriever(vectorstore=vecstore, 
                                     docstore= InMemoryStore(),
                                     child_splitter= child_splitter,
                                     parent_splitter=parent_splitter
                                     )
retreiver2 = BM25Retriever.from_documents(docs_chunks,search_kwargs={'k':1})
retreiver3 = vecstore.as_retriever(search_kwargs={"k": 2})

In [43]:
# from langchain.retrievers.document_compressors import LLMChainFilter
# from langchain.retrievers import ContextualCompressionRetriever
# from langchain.retrievers.document_compressors import LLMChainExtractor

# _filter = LLMChainFilter.from_llm(model)
# compression_retriever = ContextualCompressionRetriever(
#     base_compressor=_filter, base_retriever=retreiver2
# )

In [44]:
# compression_retriever.invoke("what is machine Learning?")

: 

In [81]:
ensemble_retriever = EnsembleRetriever(
    retrievers=[retreiver2, retreiver3], weights=[0.5, 0.5]
)

#RAG CHAIN PULLING

In [31]:

from langchain_core.prompts import ChatPromptTemplate
from langchain_core.runnables import RunnableLambda
from langchain_core.runnables.passthrough import RunnableAssign
from langchain.document_transformers import LongContextReorder

# from gpt4all import GPT4All
from operator import itemgetter

import gradio as gr

C:\Users\Win 10\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [87]:
long_reorder = RunnableLambda(LongContextReorder().transform_documents)

def docs2str(docs, title="Document"):
    out_str = ""
    for doc in docs:
        doc_name = getattr(doc, 'metadata', {}).get('Title', title)
        if doc_name: out_str += f"[Quote from {doc_name}] "
        out_str += getattr(doc, 'page_content', str(doc)) + "\n"
    return out_str

def output_puller(inputs):

    if isinstance(inputs, dict):
        inputs = [inputs]
    for token in inputs:
        if token.get('output'):
            yield token.get('output')
            
            

In [ ]:
# GPT4All.list_models()

In [54]:
chat_prompt = ChatPromptTemplate.from_template(
    "You are a document chatbot. Help the user as they ask questions about documents."
    "Try not to copy whole content but answer to the point and concisely."
    "Check weather the user question needs any response to be generated from 'Document Retrieval' or not.\n\n "
    "The following information may be useful for your response: "
    "Document Retrieval:\n{context}\n\n"
    "(Answer only from retrieval if needed.Make your response conversational)"
    "\n\nUser Question: {input}"
)

In [88]:
llm = chat_prompt | model

context_getter = itemgetter('input') | ensemble_retriever | long_reorder | docs2str
retreiver_chain = {'input': (lambda x :x)} | RunnableAssign({'context': context_getter})
generator_chain = RunnableAssign({'output' : llm}) | RunnableLambda(output_puller)

rag_chain = retreiver_chain | generator_chain


In [91]:
def chat_gen(message, history=[], return_buffer=True):
    buffer = ''
    for token in rag_chain.stream(message):
        buffer += token
        yield buffer if return_buffer else token

initial_msg = "Hello! I'm here to help with any document-related inquiries or tasks. Please feel free to ask me anything related to documents."
chatbot = gr.Chatbot(value = [[None, initial_msg]])
demo = gr.ChatInterface(chat_gen, chatbot=chatbot).queue()

try:
    demo.launch(debug=True, share=True, show_api=False)
    demo.close()
except Exception as e:
    demo.close()
    print(e)
    raise e

Running on local URL:  http://127.0.0.1:7860
Running on public URL: https://a047f8fc7ec2851b86.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from Terminal to deploy to Spaces (https://huggingface.co/spaces)


Keyboard interruption in main thread... closing server.
Killing tunnel 127.0.0.1:7860 <> https://a047f8fc7ec2851b86.gradio.live
Closing server running on port: 7860
deque mutated during iteration


RuntimeError: deque mutated during iteration